In [2]:
import cv2
import numpy as np
import matplotlib.pyplot as plt
from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets
import scipy.spatial.transform as tf
import plotly.graph_objects as gobj

In [3]:
nsa_3d_ns = np.array([[-0.078125 , -0.1875   , -0.8261623], [-0.078125 , -0.078125 , -0.8255522], [ 0.046875  , -0.1875    , -0.82176167],[ 0.046875 , -0.078125 , -0.8211517]])
T = np.array([[1.0000, 0.0000, 0.0000, 0.3408],
        [0.0000, 1.0000, 0.0000, 0.0175],
        [0.0000, 0.0000, 1.0000, 0.7682]])
scale = 1.9628406994581755

"""
assumptions:
T is from world to polycam
T needs not to be scaled
scale is multiplied to ns coords
"""

nsa_3d_pc = (nsa_3d_ns * scale) - T[:, -1].flatten()
print(nsa_3d_pc)

[[-0.49414693 -0.38553263 -2.38982499]
 [-0.49414693 -0.17084693 -2.38862746]
 [-0.24879184 -0.38553263 -2.38118725]
 [-0.24879184 -0.17084693 -2.37998998]]


In [4]:
import json
import open3d as o3d
#floor = o3d.io.read_point_cloud("/Users/liuxinqing/Documents/polycam_mate_floor/pointcloud_floor.xyz")
#floor = np.asarray(floor.points).reshape((-1,3))
ds_path = "/Users/liuxinqing/Documents/polycam_mate_floor/"
with open(f"{ds_path}/transforms.json") as f:
    transforms_json = json.load(f)


img_id_to_frame = {int(f["file_path"].split("_")[-1][:5]) : f for f in transforms_json["frames"]}

# polycam axis orientation is aligned already with nerfstudio
a, b, c, d = 0.015554840135326483, -0.0005128045313483989, -1.0, -0.8270852933415891

# sample some points
x, y = np.meshgrid(np.linspace(-1, 1, 10), np.linspace(-1, 1, 10), indexing='ij')
x = x.flatten()
y = y.flatten()
factor = 0.5
x *= factor
y *= factor
z = (-d - a * x - b * y) / c
plane_sample_pts = np.vstack([x,y,z]).reshape((-1, 3))

# let's cheat a bit by using polycam's reconstruction
min_quantile = 1e-1
max_quantile = 1-min_quantile
#((xmin, xmax), )= np.quantile(floor, [min_quantile, max_quantile], axis=0)
'''
plane_sample_pts = nsa_3d


plane_samples = gobj.Scatter3d(
    name="plane samples",
    x=plane_sample_pts[:, 0],
    y=plane_sample_pts[:, 1],
    z=plane_sample_pts[:, 2]/ 1000,
    mode='lines+markers',
    marker=dict(
        size=1,
        color="red",
    )
)

fig = gobj.Figure(
    data=[
        plane_samples,
    ],
    )

# fig.update_layout(scene_aspectmode='data', width=800, height=800)
fig.update_coloraxes(showscale=False)
fig.show()

'''

'\nplane_sample_pts = nsa_3d\n\n\nplane_samples = gobj.Scatter3d(\n    name="plane samples",\n    x=plane_sample_pts[:, 0],\n    y=plane_sample_pts[:, 1],\n    z=plane_sample_pts[:, 2]/ 1000,\n    mode=\'lines+markers\',\n    marker=dict(\n        size=1,\n        color="red",\n    )\n)\n\nfig = gobj.Figure(\n    data=[\n        plane_samples,\n    ],\n    )\n\n# fig.update_layout(scene_aspectmode=\'data\', width=800, height=800)\nfig.update_coloraxes(showscale=False)\nfig.show()\n\n'

In [27]:

nsa_3d_ns = np.array([[-0.078125 , -0.1875   , -0.8261623], 
                      [-0.078125 , -0.078125 , -0.8255522], 
                      [ 0.046875 , -0.1875   , -0.82176167],
                      [ 0.046875 , -0.078125 , -0.8211517]])
'''

nsa_3d_ns = np.array([[-0.078125 , 0.1875   , 0.8261623], 
                      [-0.078125 , 0.078125 , 0.8255522], 
                      [ 0.046875 , 0.1875   , 0.82176167],
                      [ 0.046875 , 0.078125 , 0.8211517]])
'''

T = np.array([[1.0000, 0.0000, 0.0000, 0.3408],
        [0.0000, 1.0000, 0.0000, 0.0175],
        [0.0000, 0.0000, 1.0000, 0.7682]])
scale = 1.9628406994581755

nsa_3d_pc = (nsa_3d_ns / scale) - T[:, -1].flatten()
nsa_3d_pc = nsa_3d_ns
print(nsa_3d_pc)

# Append a row to T to make it a 4x4 matrix
T = np.vstack((T, [0, 0, 0, 1]))

# Compute the inverse of T
T_inv = np.linalg.inv(T)

# Append a column of ones to nsa_3d_ns
nsa_3d_ns_homogeneous = np.hstack((nsa_3d_ns, np.ones((nsa_3d_ns.shape[0], 1))))

# Apply the inverse transformation
result = np.dot(T_inv, nsa_3d_ns_homogeneous.T).T

# The result is a 4D array, we only need the first 3 dimensions
result = result[:, :3]
print(result)

nsa_3d_ns = result

nsa_3d_pc = nsa_3d_ns / scale
# nsa_3d_ns = nsa_3d_ns * np.array([1, -1, -1])
"""
assumptions:
T is from world to polycam
T needs not to be scaled
scale is multiplied to ns coords
"""



@interact(img_id = widgets.IntSlider(min=1, max=69, step=1, value=1, continuous_update=False))
def mate_images_demo(img_id:int):
    img_path = f"{ds_path}/images/frame_{img_id:05d}.jpg"
    img = cv2.imread(img_path)
    img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
    mask = cv2.imread(f"{ds_path}/masks_2/frame_{img_id:05d}.png", cv2.IMREAD_GRAYSCALE) != 255
    frame = img_id_to_frame[img_id]
    print(frame)
    fx = frame["fl_x"]
    fy = frame["fl_y"]
    cx = frame["cx"]
    cy = frame["cy"]
    K = np.array([
        [fx, 0, cx],
        [0, fy, cy],
        [0, 0, 1],
    ])
    T = np.array(frame["transform_matrix"])
    R = T[:3, :3] 
    #R = R @ np.array([[1, 0, 0], [0, -1, 0], [0, 0, -1]])
    tvec = T[:3, -1]
    uv, _ = cv2.projectPoints(nsa_3d_pc, R, tvec, K, None)
    uv = uv.reshape((-1, 2))
    np.putmask(img[..., 1], mask, 180)
    plt.imshow(img)
    plt.scatter(uv[:, 0], uv[:, 1])
    plt.show()



[[-0.078125   -0.1875     -0.8261623 ]
 [-0.078125   -0.078125   -0.8255522 ]
 [ 0.046875   -0.1875     -0.82176167]
 [ 0.046875   -0.078125   -0.8211517 ]]
[[-0.418925   -0.205      -1.5943623 ]
 [-0.418925   -0.095625   -1.5937522 ]
 [-0.293925   -0.205      -1.58996167]
 [-0.293925   -0.095625   -1.5893517 ]]


interactive(children=(IntSlider(value=1, continuous_update=False, description='img_id', max=69, min=1), Output…

In [2]:
from neraser.colmap_read_write_model import *
from neraser.colmap_bbox import compute_object_bbox
from matplotlib.patches import Rectangle

normal_vector = np.array([-0.05711038, 0.7855485, 0.615784])
a, b, c = normal_vector
point_on_plane = np.array([0.9341631,3.826435,0.597287])
d = -np.dot(normal_vector, point_on_plane)
aa_nsa_xmin, aa_nsa_ymin, aa_nsa_xmax, aa_nsa_ymax = 0.01341, 0.3207, 1.5662, 1.8974
threshold = 5e-3
images = read_images_binary("data/lego_plenoxels/colmap/sparse/0/images.bin")
cameras = read_cameras_binary("data/lego_plenoxels/colmap/sparse/0/cameras.bin")
points = read_points3D_binary("data/lego_plenoxels/colmap/sparse/0/points3D.bin")
bbox, inlier_pts, counter = compute_object_bbox(
    "data/lego_plenoxels/colmap/sparse/0/images.bin",
    "data/lego_plenoxels/colmap/sparse/0/points3D.bin",
    "data/lego_plenoxels/masks/",
    min_quantile=threshold,
    max_quantile=1-threshold)
((xmin, ymin, zmin),(xmax, ymax, zmax)) = bbox
inlier_xyz = np.array([p.xyz for p in inlier_pts])
inlier_rgb = np.array([p.rgb for p in inlier_pts])
inside_bbox = inlier_xyz[:, 0] < xmax
inside_bbox &= inlier_xyz[:, 0] > xmin
inside_bbox &= inlier_xyz[:, 1] < ymax
inside_bbox &= inlier_xyz[:, 1] > ymin
inside_bbox &= inlier_xyz[:, 2] < zmax
inside_bbox &= inlier_xyz[:, 2] > zmin
inlier_rgb[~inside_bbox, :] = np.array([255,0,0])
inlier_xyz = inlier_xyz[inside_bbox, :]
inlier_rgb = inlier_rgb[inside_bbox, :]
rot, _ = tf.Rotation.align_vectors(normal_vector.reshape((1,3)), np.array([[0,0,1]]))
z_align = rot.from_euler("XYZ", [0, 0, np.pi*32/180]) # manually rotate around z for perfect alignment 
aa_inlier_xyz = inlier_xyz @ rot.as_matrix() @ z_align.as_matrix()
((_xmin, _ymin, _zmin),(_xmax, _ymax, _zmax)) = np.quantile(aa_inlier_xyz, [threshold/50, 1-threshold/2], axis=0)

def make_bbox_for_plotting(_xmin, _ymin, _zmin, _xmax, _ymax, _zmax):
    
    return np.array([
        [_xmin, _xmin, _xmax, _xmax, _xmin, _xmin, _xmin, _xmax, _xmax, _xmin, _xmin, _xmin, _xmax, _xmax, _xmax, _xmax],
        [_ymin, _ymax, _ymax, _ymin, _ymin, _ymin, _ymax, _ymax, _ymin, _ymin, _ymax, _ymax, _ymax, _ymax, _ymin, _ymin],
        [_zmin, _zmin, _zmin, _zmin, _zmin, _zmax, _zmax, _zmax, _zmax, _zmax, _zmax, _zmin, _zmin, _zmax, _zmax, _zmin],
    ]).T

aabb_vert = make_bbox_for_plotting(_xmin, _ymin, _zmin, _xmax, _ymax, _zmax)
aabb_vert = aabb_vert @ z_align.inv().as_matrix() @ rot.inv().as_matrix()
aa_nsa_vert = make_bbox_for_plotting(aa_nsa_xmin, aa_nsa_ymin, _zmax, aa_nsa_xmax, aa_nsa_ymax, _zmax)
nsa_vert = aa_nsa_vert @ z_align.inv().as_matrix() @ rot.inv().as_matrix()


def polygon_to_mask(img_shape, # 2d (row, col)
                    R, # 3x3 world to camera
                    T, # world to camera
                    K, # intrinsic 3x3
                    polygon, # 3d
                    distortion_coef = None,  
):
    out = np.zeros(img_shape)
    xy, _ = cv2.projectPoints(polygon, R, T, K, distortion_coef)
    xy = xy.reshape((-1, 2))
    mask = cv2.fillConvexPoly(out, xy.astype(np.int32), 255).astype(bool)
    return mask, xy


def get_bbox_from_mask(obj_mask):
    y, x = obj_mask.shape
    yy, xx = np.meshgrid(range(y), range(x), indexing='ij')
    yy, xx = yy[obj_mask], xx[obj_mask]
    xmin, xmax = np.min(xx), np.max(xx)
    ymin, ymax = np.min(yy), np.max(yy)
    return xmin, xmax, ymin, ymax


def sample_points(obj_mask,
                  colmap_img, # colmap img
                  colmap_point3Ds,
                  y_downshift=5, y_height=25):
    yy, xx = obj_mask.shape
    xmin, xmax, _, ymin = get_bbox_from_mask(obj_mask)
    ymin = min(yy, ymin+y_downshift)
    ymax = min(yy, ymin+y_height)
    _y, _x = np.meshgrid(range(ymin, ymax), range(xmin, xmax), indexing='ij')
    img_coord_candidates = np.array([_x, _y], dtype=np.int32).T.reshape((-1, 2))
    img_coord_candidates_flattened = np.ravel_multi_index((img_coord_candidates[:, 1], img_coord_candidates[:, 0]), obj_mask.shape, order='C') 
    features_pix_coord = colmap_img.xys.astype(np.uint32)
    # tracked_points_img = features_pix_coord
    # since feature coord are rounded, they could go oob; mode="clip" prevents oob access
    features_flattened = np.ravel_multi_index((features_pix_coord[:, 1], features_pix_coord[:, 0]), obj_mask.shape, order='C', mode="clip")
    tracked_candidates, feature_ind, _ = np.intersect1d(features_flattened, img_coord_candidates_flattened, return_indices=True)
    tracked_points_img = np.array(np.unravel_index(tracked_candidates, obj_mask.shape))
    inlier_mask = np.zeros(features_pix_coord.shape[0], dtype=bool)
    inlier_mask[feature_ind] = True
    point3d_ids = colmap_img.point3D_ids[inlier_mask]
    actually_tracked = point3d_ids != -1
    point3d_ids = point3d_ids[actually_tracked]
    tracked_points_img = (tracked_points_img.T)[actually_tracked]
    return tracked_points_img, point3d_ids, xmin, xmax, ymin, ymax


@interact(img_id = widgets.IntSlider(min=1, max=102, step=1, value=1, continuous_update=False))
def visualize_sample_points(img_id):
    colmap_img = images[img_id]
    filename = colmap_img.name
    obj_mask = cv2.imread(f"data/lego_plenoxels/masks/{filename}", cv2.IMREAD_GRAYSCALE) != 255
    img1 = cv2.imread(f"data/lego_plenoxels/images/{filename}")
    img1 = cv2.cvtColor(img1, cv2.COLOR_BGR2RGB)
    tracked_points, _, x0, x1, y0, y1 = sample_points(obj_mask, colmap_img, None)
    R_wc = qvec2rotmat(colmap_img.qvec)
    T_wc = colmap_img.tvec
    fx, fy, cx, cy, k1, k2, p1, p2 = cameras[colmap_img.camera_id].params
    K = np.array([
        [fx, 0, cx],
        [0, fy, cy],
        [0,  0, 1],
    ])
    d = np.array([k1, k2, p1, p2])
    _, bbox_2d = polygon_to_mask(obj_mask.shape, R_wc, T_wc, K, aabb_vert, d)
    nsa_mask, _ = polygon_to_mask(obj_mask.shape, R_wc, T_wc, K, nsa_vert, d)
    np.putmask(img1[..., 1], nsa_mask, 180) # color the patch green
    plt.gca().add_patch(Rectangle((x0, y0), x1-x0, y1-y0, fill=False, edgecolor = 'cyan')) # sample area
    plt.title(f"img {img_id} sample area:{y1-y0}x{x1-x0}; {len(tracked_points)} pts")
    plt.scatter(tracked_points[:, 1], tracked_points[:, 0], c='b', marker='.', s=1)
    plt.plot(bbox_2d[:, 0], bbox_2d[:, 1], c="r")
    plt.imshow(img1)
    plt.show()

#visualize_sample_points(1)

/var/folders/6c/zl9z2cjs3bj3shzy415bn7r40000gn/T/ipykernel_21127/582085025.py:32: UserWarning: Optimal rotation is not uniquely or poorly defined for the given sets of vectors.
  rot, _ = tf.Rotation.align_vectors(normal_vector.reshape((1,3)), np.array([[0,0,1]]))


interactive(children=(IntSlider(value=1, continuous_update=False, description='img_id', max=102, min=1), Outpu…

In [79]:
dpi = 333 
h_in, w_in = 1, 8
rep = int(w_in * dpi / 256)
range = np.arange(255, dtype=np.uint8).reshape((255, 1))
range = np.repeat(range, rep, axis=1).flatten().reshape((1,-1))
range = np.repeat(range, h_in*dpi, axis=0)
print(range.shape)
cv2.imwrite("grascale_test.png", range)

(333, 2550)


True

nerfstudio data download: https://github.com/nerfstudio-project/nerfstudio/blob/55616e1299a853c64963550a10dbd5730640cb03/nerfstudio/scripts/downloads/download_data.py#L36

In [37]:
import plotly.graph_objects as gobj

tracked_point3d_ids = set()
for img_id in range(1, 103):
    colmap_img = images[img_id]
    filename = colmap_img.name
    obj_mask = cv2.imread(f"data/lego_plenoxels/masks/{filename}", cv2.IMREAD_GRAYSCALE) != 255
    p3did = sample_points(obj_mask, colmap_img, None)[1]
    tracked_point3d_ids.update(set(p3did))
tracked_point3d_ids.remove(-1)

tracked_table_xyz = np.array([points[i].xyz for i in tracked_point3d_ids])
tracked_table_rgb = np.array([points[i].rgb for i in tracked_point3d_ids])
tracked_table_pts = gobj.Scatter3d(
    name="tracked table points",
    x=tracked_table_xyz[:, 0],
    y=tracked_table_xyz[:, 1],
    z=tracked_table_xyz[:, 2],
    mode='markers',
    marker=dict(
        size=1,
        color=tracked_table_rgb,
    )
)

def generate_3d_plane(normal_vector, point_on_plane, size=2):
    x = np.linspace(-size, size, 100)
    y = np.linspace(-size, size, 100) + 1
    x, y = np.meshgrid(x, y)
    z = (-normal_vector[0] * x - normal_vector[1] * y + np.dot(normal_vector, point_on_plane)) / normal_vector[2]
    return x, y, z

x, y, z = generate_3d_plane(normal_vector, point_on_plane, size=np.max([xmax, ymax, zmax])*0.5)

color = np.zeros_like(z)
plane = gobj.Surface(
    name="table surface",
    x=x, y=y, z=z,
    opacity=0.3,
    surfacecolor=color,
    showscale=False,
    showlegend=True,
)

point_cloud = gobj.Scatter3d(
    name="object pointcloud",
    x=inlier_xyz[:, 0],
    y=inlier_xyz[:, 1],
    z=inlier_xyz[:, 2],
    mode='markers',
    marker=dict(
        size=1,
        color=inlier_rgb
    )
)

bbox_plot = gobj.Scatter3d(
    name = 'bbox',
    x = [xmin, xmin, xmax, xmax, xmin, xmin, xmin, xmax, xmax, xmin, xmin, xmin, xmax, xmax, xmax, xmax],
    y = [ymin, ymax, ymax, ymin, ymin, ymin, ymax, ymax, ymin, ymin, ymax, ymax, ymax, ymax, ymin, ymin],
    z = [zmin, zmin, zmin, zmin, zmin, zmax, zmax, zmax, zmax, zmax, zmax, zmin, zmin, zmax, zmax, zmin],
    mode="lines"
)

mvbox_plot = gobj.Scatter3d(
    name = 'min volume box',
    x=aabb_vert[:, 0],
    y=aabb_vert[:, 1],
    z=aabb_vert[:, 2],
    mode="lines",
    marker=dict(
        color="red",
    ),
)

nsa_plot = gobj.Scatter3d(
    name = 'NSA',
    x=nsa_vert[:, 0],
    y=nsa_vert[:, 1],
    z=nsa_vert[:, 2],
    mode="lines+markers",
    marker=dict(
        size=3,
        color="green",
    ),
)


fig = gobj.Figure(
    data=[
        plane,
        point_cloud,
        mvbox_plot,
        nsa_plot,
        tracked_table_pts,
        #bbox_plot,
        #polygon,
    ],
    )

fig.update_layout(scene_aspectmode='data', width=800, height=800)
fig.update_coloraxes(showscale=False)
fig.show()


In [73]:
np.savetxt("nsa_vert_colmap.npy", nsa_vert[:4, :])
np.savetxt("plane_eqn_colmap.npy", np.array([a, b, c, d]))
import pickle
img_id_to_tracked_points = dict()

for img_id in range(1, 103):
    obj_mask = cv2.imread(f"data/lego_plenoxels/masks/{filename}", cv2.IMREAD_GRAYSCALE) != 255
    tracked_pts, p3d_idx, _, _, _, _ = sample_points(obj_mask, images[img_id], None)
    if tracked_pts.shape[0]:
        print(img_id, tracked_pts.shape, p3d_idx.shape)
        info = np.hstack([tracked_pts, np.array([points[p].xyz for p in p3d_idx])])
        img_id_to_tracked_points[img_id] = info

pickle.dump(img_id_to_tracked_points, open("img_id_to_point_colmap.pickle", 'wb')) 


1 (47, 2) (47,)
2 (59, 2) (59,)
3 (32, 2) (32,)
4 (48, 2) (48,)
5 (63, 2) (63,)
6 (3, 2) (3,)
7 (9, 2) (9,)
8 (1, 2) (1,)
9 (20, 2) (20,)
10 (38, 2) (38,)
11 (60, 2) (60,)
12 (43, 2) (43,)
13 (47, 2) (47,)
14 (23, 2) (23,)
15 (24, 2) (24,)
16 (40, 2) (40,)
17 (77, 2) (77,)
18 (66, 2) (66,)
19 (7, 2) (7,)
20 (6, 2) (6,)
21 (31, 2) (31,)
22 (25, 2) (25,)
23 (36, 2) (36,)
24 (40, 2) (40,)
25 (26, 2) (26,)
26 (9, 2) (9,)
27 (14, 2) (14,)
28 (22, 2) (22,)
29 (35, 2) (35,)
30 (49, 2) (49,)
31 (22, 2) (22,)
32 (38, 2) (38,)
33 (19, 2) (19,)
34 (30, 2) (30,)
35 (15, 2) (15,)
36 (47, 2) (47,)
37 (15, 2) (15,)
38 (84, 2) (84,)
39 (27, 2) (27,)
40 (36, 2) (36,)
41 (3, 2) (3,)
42 (56, 2) (56,)
43 (57, 2) (57,)
44 (40, 2) (40,)
45 (17, 2) (17,)
47 (1, 2) (1,)
48 (28, 2) (28,)
49 (42, 2) (42,)
50 (12, 2) (12,)
51 (21, 2) (21,)
53 (8, 2) (8,)
54 (38, 2) (38,)
55 (35, 2) (35,)
56 (32, 2) (32,)
57 (31, 2) (31,)
58 (2, 2) (2,)
60 (22, 2) (22,)
61 (27, 2) (27,)
62 (27, 2) (27,)
63 (4, 2) (4,)
64 (20, 2) 

In [74]:
import pickle
plane_eqn = np.loadtxt("plane_eqn_colmap.npy") #(4,)
nsa_vert = np.loadtxt("nsa_vert_colmap.npy") # (4,3)
print(nsa_vert.shape)
img_id_to_tracked_points = pickle.load(open("img_id_to_point_colmap.pickle", 'rb'))
for img_id, pts in img_id_to_tracked_points.items():
    img_coord = pts[:, :2]
    xyz_coord = pts[:, 2:]
    print(img_coord.shape)



(4, 3)
(47, 2)
(59, 2)
(32, 2)
(48, 2)
(63, 2)
(3, 2)
(9, 2)
(1, 2)
(20, 2)
(38, 2)
(60, 2)
(43, 2)
(47, 2)
(23, 2)
(24, 2)
(40, 2)
(77, 2)
(66, 2)
(7, 2)
(6, 2)
(31, 2)
(25, 2)
(36, 2)
(40, 2)
(26, 2)
(9, 2)
(14, 2)
(22, 2)
(35, 2)
(49, 2)
(22, 2)
(38, 2)
(19, 2)
(30, 2)
(15, 2)
(47, 2)
(15, 2)
(84, 2)
(27, 2)
(36, 2)
(3, 2)
(56, 2)
(57, 2)
(40, 2)
(17, 2)
(1, 2)
(28, 2)
(42, 2)
(12, 2)
(21, 2)
(8, 2)
(38, 2)
(35, 2)
(32, 2)
(31, 2)
(2, 2)
(22, 2)
(27, 2)
(27, 2)
(4, 2)
(20, 2)
(46, 2)
(32, 2)
(18, 2)
(10, 2)
(25, 2)
(21, 2)
(27, 2)
(30, 2)
(27, 2)
(1, 2)
(22, 2)
(11, 2)
(2, 2)
(2, 2)
(16, 2)
(26, 2)
(44, 2)
(21, 2)
(3, 2)
(7, 2)
(34, 2)
(45, 2)
(59, 2)
(10, 2)
(62, 2)
(49, 2)
(13, 2)
(5, 2)
(11, 2)
(44, 2)
(25, 2)
(38, 2)
(39, 2)
(6, 2)
(32, 2)


In [ ]:
def deproject_points():
    # first get the corresponding depth
    # then get the inverse of K
    # undistort feature xy, deproject, apply depth
    return None

def use_deproject_points(img_id):
    colmap_img = images[img_id]
    fx, fy, cx, cy, k1, k2, p1, p2 = cameras[colmap_img.camera_id].params
    K_inv = np.array([
        1/fx, 0, -cx/fx,
        0, 1/fy, -cy/fy,
        0, 0 ,1
    ])
    return None


In [51]:
# investigate discrepency btwn colmap transform and nerfstudio transform
import json
with open("data/lego_plenoxels/transforms.json") as f:
    ns_transforms = json.load(f)
# print(ns_transforms["applied_transform"])
id_to_transform = {int(i["colmap_im_id"]): np.array(i["transform_matrix"] ) for i in ns_transforms["frames"]}
colmap_to_ns = np.array([
    [ 0.0237,  0.5714, -0.8204,  0.4603],
    [ 0.9987,  0.0237,  0.0453,  0.5088],
    [ 0.0453, -0.8204, -0.5701,  0.0188],
    [0, 0, 0, 1],
])
scale_factor = 0.18077436331220487
for iid in range(1, 103):
    colmap_cam_t = images[iid].tvec
    colmap_R = qvec2rotmat(images[iid].qvec)
    colmap_t = np.hstack([colmap_R, colmap_cam_t.reshape((3,1))])
    colmap_t = np.vstack([colmap_t, np.array([0,0,0,1])])
    ns_t = colmap_to_ns @ colmap_t
    ns_t[:-1, -1] *= scale_factor
    gt = id_to_transform[iid]
    diff = gt - ns_t

(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)
(4, 4)


In [17]:
print(aa_inlier_xyz.shape)
bottom = aa_inlier_xyz[aa_inlier_xyz[:, 2] > _zmax * 0.85]
print(bottom.shape)

btm_plot = gobj.Scatter(
    x=bottom[:, 0], 
    y=bottom[:, 1],
    mode="markers",
)
fig = gobj.Figure(
    data=[
        btm_plot,
    ]
)
fig.show()
# in the plot, manually select bottom left and top right to form NSA in axis aligned mode

(8987, 3)
(185, 3)


In [10]:
from scipy import ndimage
def dilate_mask(mask_img, radius, invert=False):
    mask_img = np.bitwise_not(mask_img) if invert else mask_img
    dilated = ndimage.maximum_filter(mask_img, size=radius).astype(np.uint8)
    # binarize
    dilated[dilated>0] = 255
    return dilated

#@interact(img_id = widgets.IntSlider(min=1, max=69, step=1, value=1, continuous_update=False))
def dilate_mask_demo(img_id):
    img_name = f"/Users/bzs/Downloads/polycam_mate_floor/masks_2/frame_000{img_id:02d}.png"
    mask_img = cv2.imread(img_name, cv2.IMREAD_GRAYSCALE)
    dilated = dilate_mask(mask_img, 9, invert=True)
    cv2.imwrite(f"/Users/bzs/Downloads/polycam_mate_floor/masks_2_dilated/frame000{img_id:02d}_mask001.png", dilated)
    # plt.gray()  # show the filtered result in grayscale
    # fig = plt.figure()
    # ax1 = fig.add_subplot(121)  # left side
    # ax2 = fig.add_subplot(122)  # right side
    # ax1.imshow(mask_img)
    # ax2.imshow(dilated)
    # plt.show()
for img_id in range(1, 70):
    dilate_mask_demo(img_id)

0.9997689613165606

In [22]:
plane_points = np.array(
    [[ 0.09619215,  0.18419623, -0.27866834],
     [ 0.09370056,  0.17330916, -0.3003558 ],
     [ 0.09418262,  0.19857953, -0.27315882],
     [ 0.08380522, -0.18537372, -0.011829  ],
     [ 0.07928248, -0.18414381, -0.0044587 ],
     [ 0.08964445, -0.18383668, -0.01852112],
     [-0.00375274, -0.14307953,  0.1119528 ],
     [-0.00676645, -0.13449907,  0.11913031],
     [-0.00565832, -0.15868491,  0.10510083],
     [-0.23815173,  0.01478208,  0.02895552],
     [-0.25153425,  0.03111171,  0.03467682],
     [-0.23558566, -0.00102766,  0.02254268],
     [-0.19367798,  0.09395444,  0.11415317],
     [-0.20212367,  0.1110208 ,  0.11448489],
     [-0.20050208,  0.07870765,  0.11527123],
     [-0.10122801,  0.25870624,  0.15247521],
     [-0.09928557,  0.26774612,  0.14757934],
     [-0.11439849,  0.25597614,  0.16148819],
     [-0.0189445 ,  0.40594056, -0.05700587],
     [-0.0194651 ,  0.4193155 , -0.0729074 ],
     [-0.02585882,  0.40596634, -0.04706441],
     [ 0.0656293 ,  0.33922005, -0.17095272],
     [ 0.06939287,  0.33703187, -0.18619718],
     [ 0.05656687,  0.35268608, -0.16519219],
     [-0.01315877,  0.39768305,  0.04828297],
     [-0.01366454,  0.41207817,  0.03969196],
     [-0.01842888,  0.39572006,  0.05479426]]
)

plane_norm = np.array([-0.7358716726303101, -0.14783693850040436, -1, -0.013480226509273052])
x0, y0, z0, intercept = plane_norm

nerf_bbox = np.array([[ 0.0114, -0.1916, -0.0216],
        [-0.5252, -0.1620, -0.3944],
        [ 0.2723, -0.1808, -0.3962],
        [-0.2642, -0.1512, -0.7690],
        [ 0.0221,  0.2614, -0.0010],
        [-0.5144,  0.2910, -0.3738],
        [ 0.2830,  0.2722, -0.3756],
        [-0.2535,  0.3019, -0.7485]
])

plane_pts = gobj.Scatter3d(
    name='plane points',
    x=plane_points[:, 0],
    y=plane_points[:, 1],
    z=plane_points[:, 2],
    mode="markers"
)

nerf_bbx_pts = gobj.Scatter3d(
    name='plane points',
    x=nerf_bbox[:, 0],
    y=nerf_bbox[:, 1],
    z=nerf_bbox[:, 2],
    mode="markers+lines"
)

# xmin, xmax, ymin, ymax, zmin, zmax = (0.2830, -0.5252, 0.3019, -0.1916, -0.0010, -0.7690)
# nerf_bbx_pts = gobj.Scatter3d(
#     name = 'nerf_bbox',
#     x = [xmin, xmin, xmax, xmax, xmin, xmin, xmin, xmax, xmax, xmin, xmin, xmin, xmax, xmax, xmax, xmax],
#     y = [ymin, ymax, ymax, ymin, ymin, ymin, ymax, ymax, ymin, ymin, ymax, ymax, ymax, ymax, ymin, ymin],
#     z = [zmin, zmin, zmin, zmin, zmin, zmax, zmax, zmax, zmax, zmax, zmax, zmin, zmin, zmax, zmax, zmin],
#     mode="lines"
# )

fig = gobj.Figure(
    data=[
        #plane_pts,
        #nerf_bbx_pts,
    ],
    )

fig.update_layout(scene_aspectmode='data', width=800, height=800)

(400,)


In [8]:
from neraser.colmap_read_write_model import *
import scipy.spatial.transform as tf
from matplotlib.patches import Polygon
images = read_images_binary("data/lego_plenoxels/colmap/sparse/0/images.bin")
cameras = read_cameras_binary("data/lego_plenoxels/colmap/sparse/0/cameras.bin")
points = read_points3D_binary("data/lego_plenoxels/colmap/sparse/0/points3D.bin")
for img1 in images.values():
        ids = img1.point3D_ids
        valid = np.array([p in points for p in ids], dtype=bool)
        img1_uv = img1.xys[valid]
        img1_xyz = np.array([points[p].xyz for p in img1.point3D_ids[valid]])
        print(f"{img1_xyz.shape=} {img1_uv.shape=}")
        qvec = img1.qvec
        tvec = img1.tvec
        fx, fy, cx, cy, k1, k2, p1, p2 = cameras[img1.camera_id].params
        R = qvec2rotmat(qvec)
        K = np.array([
                [fx, 0, cx],
                [0, fy, cy],
                [0,  0, 1],
        ])
        uv_, _ = cv2.projectPoints(img1_xyz[:, :], R, tvec, K, np.array([k1, k2, p1, p2]))
        uv_ = uv_.reshape((-1, 2))
        diff = np.linalg.norm(img1_uv - uv_, axis=1).mean()
        print(f"{diff=}")

img1_xyz.shape=(1315, 3) img1_uv.shape=(1315, 2)
diff=0.6973125454057866
img1_xyz.shape=(876, 3) img1_uv.shape=(876, 2)
diff=0.7620112048799069
img1_xyz.shape=(1764, 3) img1_uv.shape=(1764, 2)
diff=0.6922902611080569
img1_xyz.shape=(665, 3) img1_uv.shape=(665, 2)
diff=0.6748791063200681
img1_xyz.shape=(1701, 3) img1_uv.shape=(1701, 2)
diff=0.6178370688197932
img1_xyz.shape=(1221, 3) img1_uv.shape=(1221, 2)
diff=0.8314066121300889
img1_xyz.shape=(1533, 3) img1_uv.shape=(1533, 2)
diff=0.6868425499132977
img1_xyz.shape=(946, 3) img1_uv.shape=(946, 2)
diff=0.7422064851020309
img1_xyz.shape=(1230, 3) img1_uv.shape=(1230, 2)
diff=0.8069557279940286
img1_xyz.shape=(1565, 3) img1_uv.shape=(1565, 2)
diff=0.9130278787709021
img1_xyz.shape=(2130, 3) img1_uv.shape=(2130, 2)
diff=0.6163052454365027
img1_xyz.shape=(1807, 3) img1_uv.shape=(1807, 2)
diff=0.7933358631838977
img1_xyz.shape=(975, 3) img1_uv.shape=(975, 2)
diff=0.9536993127251812
img1_xyz.shape=(2191, 3) img1_uv.shape=(2191, 2)
diff=0.644

In [9]:
def polygon_to_mask(img_shape, # 2d (row, col)
                    R, # 3x3 world to camera
                    T, # world to camera
                    K, # intrinsic 3x3
                    polygon, # 3d
                    distortion_coef = None,  
):
    out = np.zeros(img_shape)
    xy, _ = cv2.projectPoints(polygon, R, T, K, distortion_coef)
    xy = xy.reshape((-1, 2))
    mask = cv2.fillConvexPoly(out, xy.astype(np.int32), 255).astype(bool)
    return mask, xy


@interact(img_id = widgets.IntSlider(min=1, max=102, step=1, value=1, continuous_update=False))
def visualize_polygon_mask(img_id):
    colmap_img = images[img_id]
    filename = colmap_img.name
    obj_mask = cv2.imread(f"data/lego_plenoxels/masks/{filename}", cv2.IMREAD_GRAYSCALE) != 255
    img1 = cv2.imread(f"data/lego_plenoxels/images/{filename}")
    img1 = cv2.cvtColor(img1, cv2.COLOR_BGR2RGB)
    x0, x1, y0, y1 = get_bbox_from_mask(obj_mask)
    R_wc = qvec2rotmat(colmap_img.qvec)
    T_wc = colmap_img.tvec
    fx, fy, cx, cy, k1, k2, p1, p2 = cameras[colmap_img.camera_id].params
    K = np.array([
        [fx, 0, cx],
        [0, fy, cy],
        [0,  0, 1],
    ])
    mask, polygon_2d = polygon_to_mask(img1.shape[:-1],  R_wc, T_wc, K, polygon_vertices, np.array([k1, k2, p1, p2]))
    np.putmask(img1[..., 1], mask, 255) # color the patch green
    plt.imshow(img1)
    plt.scatter(polygon_2d[:, 0], polygon_2d[:, 1])
    # plt.gca().add_patch(Polygon(polygon_2d, fill=False, edgecolor = 'cyan'))
    plt.show()

# visualize_polygon_mask(1)

interactive(children=(IntSlider(value=1, continuous_update=False, description='img_id', max=102, min=1), Outpu…

In [ ]:
from neraser.colmap_read_write_model import *


In [39]:
counts = np.array([v for v in counter.values()])
fig = gobj.Figure(data=[gobj.Histogram(x=counts)])
fig.update_layout(
    title_text="Histogram of number of 2d feature points per 3d point for Lego Plenoxel",
    xaxis_title_text='Number of 2D correspondences', # xaxis label
    yaxis_title_text='Count of 3D points', # yaxis label
    width=800,
    height=800,
)
fig.show()


In [40]:
import scipy.spatial.transform as tf
rot_radians = np.linspace(0, np.pi * 0.5, 90)
rot_matt = np.array([np.cos(rot_radians), -np.sin(rot_radians), np.sin(rot_radians), np.cos(rot_radians)]).reshape((2,2,-1))
rr = inlier_xyz[:, 1:] @ rot_matt
rot_matt = np.array([np.cos(rot_radians), -np.sin(rot_radians), np.sin(rot_radians), np.cos(rot_radians)]).reshape((2,2, -1))
rr = np.einsum("li,ijk->ljk", inlier_xyz[:, 1:], rot_matt)
obj_points = inlier_xyz
areas = np.zeros_like(rot_radians)
rot_mat = np.array([np.cos(rot_radians), -np.sin(rot_radians), np.sin(rot_radians), np.cos(rot_radians)])
for idx, rad in enumerate(rot_radians):
    # TODO one matrix mul
    rot_mat = np.array([[np.cos(rad), -np.sin(rad)], [np.sin(rad), np.cos(rad)]])
    rotated_pts = obj_points[:, 1:] @ rot_mat
    ((min_x, min_y), (max_x, max_y)) = np.quantile(rotated_pts, [0.05, 0.95], axis=0)
    areas[idx] = (max_x - min_x) * (max_y - min_y)
min_rotation = np.argmin(areas)
min_rotation = 34
rad = rot_radians[min_rotation]
rot_mat = np.array([[np.cos(rad), -np.sin(rad)], [np.sin(rad), np.cos(rad)]])
print(rot_mat)
yz = obj_points[:, 1:] @ rot_mat
projected = gobj.Scatter3d(
    name="rotated yz",
    #x=obj_points[:, 0],
    x=np.zeros_like(obj_points[:, 0]),
    y=yz[:, 0],
    z=yz[:, 1],
    mode='markers',
    marker=dict(
        size=1,
        color=inlier_rgb
    )
)
fig2 = gobj.Figure(data=[projected,])
fig2.update_layout(scene_aspectmode='data', width=800, height=800)
fig2.show()


[[ 0.82529073 -0.56470808]
 [ 0.56470808  0.82529073]]


In [24]:
rot_radians = np.linspace(0, np.pi * 0.5, 90)
def find_mvbb(points, rot_radians, num_iter=1):
    obj_points = points.copy()
    rot_matt = np.array([np.cos(rot_radians), -np.sin(rot_radians), np.sin(rot_radians), np.cos(rot_radians)]).reshape((2,2,-1))
    overall_rot_mat = np.eye(3)
    for iteration in range(1, num_iter+1):
        xyz_angle = np.zeros((3,))
        print(f"{iteration=}")
        for ax in range(3):
            pts = np.delete(obj_points, ax, axis=1)
            rr = np.einsum("li,ijk->ljk", pts, rot_matt) #n, 2, 90
            bb = np.quantile(rr, [0.05, 0.95], axis=0)
            ((x, y), (X, Y)) = bb
            areas = (X-x) * (Y-y)
            min_angle = np.argmin(areas)
            print(f"axis={ax}; {min_angle=}")
            xyz_angle[ax] = rot_radians[min_angle]
            overall_rot_mat = tf.Rotation.from_euler('XYZ', xyz_angle).as_matrix()
            obj_points = inlier_xyz @ overall_rot_mat
    return overall_rot_mat
obj_points = inlier_xyz.copy()
overall_rot_mat = find_mvbb(obj_points, rot_radians, 8)
print(overall_rot_mat)
bbox = np.quantile(obj_points, [0.01, 0.99], axis=0)
((xx,yy,zz),(XX,YY,ZZ)) = bbox;
print(f"volume={(XX-xx)*(YY-yy)*(ZZ-zz)}")
zeros = np.zeros((obj_points.shape[0]),)
projected = gobj.Scatter3d(
    name="rotated yz",
    #x=zeros,
    x=obj_points[:, 0],
    y=obj_points[:, 1],
    z=obj_points[:, 2],
    mode='markers',
    marker=dict(
        size=1,
        color=inlier_rgb
    )
)
gobj.Figure(data=[projected,]).show()

iteration=1
axis=0; min_angle=34
axis=1; min_angle=57
axis=2; min_angle=87
iteration=2
axis=0; min_angle=64
axis=1; min_angle=52
axis=2; min_angle=3
iteration=3
axis=0; min_angle=56
axis=1; min_angle=55
axis=2; min_angle=7
iteration=4
axis=0; min_angle=61
axis=1; min_angle=54
axis=2; min_angle=4
iteration=5
axis=0; min_angle=58
axis=1; min_angle=55
axis=2; min_angle=6
iteration=6
axis=0; min_angle=59
axis=1; min_angle=54
axis=2; min_angle=5
iteration=7
axis=0; min_angle=60
axis=1; min_angle=54
axis=2; min_angle=5
iteration=8
axis=0; min_angle=58
axis=1; min_angle=55
axis=2; min_angle=6
[[ 0.56154471 -0.05968884  0.82529073]
 [ 0.75585549  0.44282723 -0.48227225]
 [-0.33667493  0.89461796  0.29378342]]
volume=17.68661475007508


In [103]:
np.savetxt("lego.txt", inlier_xyz, fmt="%.6f")

In [41]:
import scipy.spatial.transform as tf
from matplotlib.patches import Rectangle
random_R = tf.Rotation.from_euler('XYZ',[45, 0, 0])
print(random_R.as_matrix())
bbox_vertices = np.array([
    [xmin, xmin, xmax, xmax, xmin, xmin, xmin, xmax, xmax, xmin],
    [ymin, ymax, ymax, ymin, ymin, ymin, ymax, ymax, ymin, ymin],
    [zmin, zmin, zmin, zmin, zmin, zmax, zmax, zmax, zmax, zmax],
])
bbox_rotated = np.dot(random_R.as_matrix(), bbox_vertices)
bbox_plot = gobj.Scatter3d(
    name = 'bbox',
    x = bbox_vertices[0, :],
    y = bbox_vertices[1, :],
    z = bbox_vertices[2, :],
    mode="lines"
)

bbox_plot_rot = gobj.Scatter3d(
    name = 'bbox_rotated',
    x = bbox_rotated[0, :],
    y = bbox_rotated[1, :],
    z = bbox_rotated[2, :],
    mode="lines"
)

fig = gobj.Figure(
    data=[
        #point_cloud,
        bbox_plot,
        bbox_plot_rot
    ],
    )

bbox_r_x = bbox_rotated[:, 3] - bbox_rotated[:, 0]
bbox_r_y = bbox_rotated[:, 1] - bbox_rotated[:, 0]
bbox_r_z = bbox_rotated[:, 5] - bbox_rotated[:, 0]
bbox_r_x = bbox_r_x / np.linalg.norm(bbox_r_x)
bbox_r_y = bbox_r_y / np.linalg.norm(bbox_r_y)
bbox_r_z = bbox_r_z / np.linalg.norm(bbox_r_z)
bbox_rot_mat = np.array([bbox_r_x, bbox_r_y, bbox_r_z]).T
bbox_rot_inv = tf.Rotation.from_matrix(bbox_rot_mat)
fig.update_layout(scene_aspectmode='data')
fig.show()


[[ 1.          0.         -0.        ]
 [-0.          0.52532199 -0.85090352]
 [ 0.          0.85090352  0.52532199]]


Cells below are scratch, they might not run

In [43]:
@interact(img_id=widgets.IntSlider(min=1, max=102, step=1, value=1))
def check_one_image(img_id: int):
    mask1 = cv2.imread(f"data/lego_plenoxels/masks/frame_{img_id:05}.png", cv2.IMREAD_GRAYSCALE)
    img1 = cv2.imread(f"data/lego_plenoxels/images/frame_{img_id:05}.png")
    img1 = cv2.cvtColor(img1, cv2.COLOR_BGR2RGB)
    bg_mask = ~(mask1 == 0)
    just_object = img1.copy()
    just_object[bg_mask, :] = 255
    plt.imshow(just_object)
    plt.show()

interactive(children=(IntSlider(value=1, description='img_id', max=102, min=1), Output()), _dom_classes=('widg…

In [10]:
from neraser.colmap_read_write_model import read_images_binary
images = read_images_binary("data/lego_plenoxels/colmap/sparse/0/images.bin")
filename_to_img = {img.name : img for img in images.values()}

def get_bbox_from_mask(obj_mask):
    y, x = obj_mask.shape
    yy, xx = np.meshgrid(range(y), range(x), indexing='ij')
    yy, xx = yy[obj_mask], xx[obj_mask]
    xmin, xmax = np.min(xx), np.max(xx)
    ymin, ymax = np.min(yy), np.max(yy)
    return xmin, xmax, ymin, ymax


from matplotlib.patches import Rectangle

@interact(img_id = widgets.IntSlider(min=1, max=102, step=1, value=1, continuous_update=False))
def visualize_inlier(img_id):
    filename = f"frame_{img_id:05}.png"
    colmap_img = filename_to_img[filename]
    obj_mask = cv2.imread(f"data/lego_plenoxels/masks/{filename}", cv2.IMREAD_GRAYSCALE) != 255
    #img = filename_to_img[filename]
    y, x = obj_mask.shape
    yy, xx = np.meshgrid(range(y), range(x), indexing='ij')
    features_pix_coord = colmap_img.xys.astype(np.int32)
    features_flattened = np.ravel_multi_index((features_pix_coord[:, 1], features_pix_coord[:, 0]), obj_mask.shape, order='C', mode="clip")
    img_coord = np.array([xx[obj_mask], yy[obj_mask]], dtype=np.int32).T
    img_coord_falttened = np.ravel_multi_index((img_coord[:, 1], img_coord[:, 0]), obj_mask.shape, order='C') 
    _, inlier_ind, _ = np.intersect1d(features_flattened, img_coord_falttened, return_indices=True)
    inlier_mask = np.zeros((features_pix_coord.shape[0], ), dtype=bool)
    inlier_mask[inlier_ind] = 1
    inlier_xx, inlier_yy = colmap_img.xys[inlier_mask].T 
    img1 = cv2.imread(f"data/lego_plenoxels/images/{filename}")
    img1 = cv2.cvtColor(img1, cv2.COLOR_BGR2RGB)
    plt.imshow(img1)
    plt.scatter(inlier_xx, inlier_yy, c='b', marker='.', s=0.4)
    x0, x1, y0, y1 = get_bbox_from_mask(obj_mask)
    plt.gca().add_patch(Rectangle((x0, y0), x1-x0, y1-y0, fill=False, edgecolor = 'cyan'))
    plt.show()


interactive(children=(IntSlider(value=1, continuous_update=False, description='img_id', max=102, min=1), Outpu…

(60454, 3)


In [49]:
normal_vector = np.array([-0.05711038,0.7855485,0.615784])
point_on_plane = np.array([0.9341631, 3.826435,  0.597287])

def generate_3d_plane(normal_vector, point_on_plane, size=10):
    # Generate a grid of points in the xy-plane
    x = np.linspace(-size, size, 100)
    y = np.linspace(-size, size, 100)
    x, y = np.meshgrid(x, y)

    # Calculate the z-coordinate for each point on the plane using the normal equation
    z = (-normal_vector[0] * x - normal_vector[1] * y + np.dot(normal_vector, point_on_plane)) / normal_vector[2]

    return x, y, z

# Define the normal vector and a point on the plane
normal_vector = np.array([1, 2, -1])
point_on_plane = np.asarray(table.points)[42, :]
print(point_on_plane)

# Generate 3D plane coordinates
x, y, z = generate_3d_plane(normal_vector, point_on_plane)

# Create a 3D surface plot using Plotly
color = np.zeros_like(z)
fig = gobj.Figure(data=[gobj.Surface(x=x, y=y, z=z,
                                 opacity=0.5,
                                 surfacecolor=color,
                                 #surfacecolor=[0.1, 0.1],
                                 )])

# Set layout options
fig.update_layout(scene=dict(aspectmode="data"))
fig.update_layout(title="3D Plane using Normal Equation")
fig.update_layout(scene=dict(
                    xaxis_title='X Axis',
                    yaxis_title='Y Axis',
                    zaxis_title='Z Axis'))

fig.update(layout_showlegend=False)

# Show the plot
fig.show()

[0.9341631 3.826435  0.597287 ]
